# Machine Learning Pipeline - Fake News Detection
- Author: Naufal Rahfi Anugerah

## Import Required Library

In [1]:
import tensorflow as tf
import tensorflow_transform as tft

import pandas as pd
import zipfile as zf
import os

from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Transform, Trainer, Tuner
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext

from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy 
from tfx.dsl.components.common.resolver import Resolver 

from tfx.types.standard_artifacts import Model, ModelBlessing
from tfx.types import Channel 

from tfx.components import Tuner
from tfx.components import Evaluator

from tfx.proto import trainer_pb2
from tfx.proto import example_gen_pb2

## Data Configuration

### Download Dataset

In [2]:
!kaggle datasets download -d clmentbisaillon/fake-and-real-news-dataset

!mkdir raw

!move fake-and-real-news-dataset.zip raw/

Dataset URL: https://www.kaggle.com/datasets/clmentbisaillon/fake-and-real-news-dataset
License(s): CC-BY-NC-SA-4.0




  0%|          | 0.00/41.0M [00:00<?, ?B/s]
  2%|▏         | 1.00M/41.0M [00:00<00:37, 1.12MB/s]
  5%|▍         | 2.00M/41.0M [00:01<00:19, 2.05MB/s]
  7%|▋         | 3.00M/41.0M [00:01<00:15, 2.65MB/s]
 10%|▉         | 4.00M/41.0M [00:01<00:13, 2.91MB/s]
 12%|█▏        | 5.00M/41.0M [00:01<00:11, 3.39MB/s]
 15%|█▍        | 6.00M/41.0M [00:02<00:12, 2.87MB/s]
 17%|█▋        | 7.00M/41.0M [00:02<00:10, 3.26MB/s]
 20%|█▉        | 8.00M/41.0M [00:02<00:10, 3.39MB/s]
 22%|██▏       | 9.00M/41.0M [00:03<00:09, 3.51MB/s]
 24%|██▍       | 10.0M/41.0M [00:03<00:09, 3.29MB/s]
 27%|██▋       | 11.0M/41.0M [00:03<00:09, 3.25MB/s]
 29%|██▉       | 12.0M/41.0M [00:04<00:09, 3.19MB/s]
 32%|███▏      | 13.0M/41.0M [00:04<00:09, 3.01MB/s]
 34%|███▍      | 14.0M/41.0M [00:05<00:09, 2.84MB/s]
 37%|███▋      | 15.0M/41.0M [00:05<00:09, 2.75MB/s]
 39%|███▉      | 16.0M/41.0M [00:05<00:09, 2.79MB/s]
 41%|████▏     | 17.0M/41.0M [00:06<00:08, 3.00MB/s]
 44%|████▍     | 18.0M/41.0M [00:06<00:08, 2.85MB/s]
 

        1 file(s) moved.


### Extract Files

In [3]:
files = "raw/fake-and-real-news-dataset.zip"
zip = zf.ZipFile(files, 'r')
zip.extractall('raw/')
zip.close()

### Data Loading

In [4]:
true = pd.read_csv("raw/True.csv")
fake = pd.read_csv("raw/Fake.csv")

In [5]:
true.head(len(true))

title  \
0      As U.S. budget fight looms, Republicans flip t...   
1      U.S. military to accept transgender recruits o...   
2      Senior U.S. Republican senator: 'Let Mr. Muell...   
3      FBI Russia probe helped by Australian diplomat...   
4      Trump wants Postal Service to charge 'much mor...   
...                                                  ...   
21412  'Fully committed' NATO backs new U.S. approach...   
21413  LexisNexis withdrew two products from Chinese ...   
21414  Minsk cultural hub becomes haven from authorities   
21415  Vatican upbeat on possibility of Pope Francis ...   
21416  Indonesia to buy $1.14 billion worth of Russia...   

                                                    text       subject  \
0      WASHINGTON (Reuters) - The head of a conservat...  politicsNews   
1      WASHINGTON (Reuters) - Transgender people will...  politicsNews   
2      WASHINGTON (Reuters) - The special counsel inv...  politicsNews   
3      WASHINGTON (Reuters) - Trump campaign adviser ...  politicsNews   
4      SEATTLE/WASHINGTON (Reuters) - President Donal...  politicsNews   
...                                                  ...           ...   
21412  BRUSSELS (Reuters) - NATO allies on Tuesday we...     worldnews   
21413  LONDON (Reuters) - LexisNexis, a provider of l...     worldnews   
21414  MINSK (Reuters) - In the shadow of disused Sov...     worldnews   
21415  MOSCOW (Reuters) - Vatican Secretary of State ...     worldnews   
21416  JAKARTA (Reuters) - Indonesia will buy 11 Sukh...     worldnews   

                     date  
0      December 31, 2017   
1      December 29, 2017   
2      December 31, 2017   
3      December 30, 2017   
4      December 29, 2017   
...                   ...  
21412    August 22, 2017   
21413    August 22, 2017   
21414    August 22, 2017   
21415    August 22, 2017   
21416    August 22, 2017   

[21417 rows x 4 columns]

In [6]:
fake.head(len(fake))

title  \
0       Donald Trump Sends Out Embarrassing New Year’...   
1       Drunk Bragging Trump Staffer Started Russian ...   
2       Sheriff David Clarke Becomes An Internet Joke...   
3       Trump Is So Obsessed He Even Has Obama’s Name...   
4       Pope Francis Just Called Out Donald Trump Dur...   
...                                                  ...   
23476  McPain: John McCain Furious That Iran Treated ...   
23477  JUSTICE? Yahoo Settles E-mail Privacy Class-ac...   
23478  Sunnistan: US and Allied ‘Safe Zone’ Plan to T...   
23479  How to Blow $700 Million: Al Jazeera America F...   
23480  10 U.S. Navy Sailors Held by Iranian Military ...   

                                                    text      subject  \
0      Donald Trump just couldn t wish all Americans ...         News   
1      House Intelligence Committee Chairman Devin Nu...         News   
2      On Friday, it was revealed that former Milwauk...         News   
3      On Christmas day, Donald Trump announced that ...         News   
4      Pope Francis used his annual Christmas Day mes...         News   
...                                                  ...          ...   
23476  21st Century Wire says As 21WIRE reported earl...  Middle-east   
23477  21st Century Wire says It s a familiar theme. ...  Middle-east   
23478  Patrick Henningsen  21st Century WireRemember ...  Middle-east   
23479  21st Century Wire says Al Jazeera America will...  Middle-east   
23480  21st Century Wire says As 21WIRE predicted in ...  Middle-east   

                    date  
0      December 31, 2017  
1      December 31, 2017  
2      December 30, 2017  
3      December 29, 2017  
4      December 25, 2017  
...                  ...  
23476   January 16, 2016  
23477   January 16, 2016  
23478   January 15, 2016  
23479   January 14, 2016  
23480   January 12, 2016  

[23481 rows x 4 columns]

### Combine the Dataset

In [7]:
true['class'] = 1
fake['class'] = 0

combine = pd.concat([true, fake], axis=0)
combine.head(len(combine))

title  \
0      As U.S. budget fight looms, Republicans flip t...   
1      U.S. military to accept transgender recruits o...   
2      Senior U.S. Republican senator: 'Let Mr. Muell...   
3      FBI Russia probe helped by Australian diplomat...   
4      Trump wants Postal Service to charge 'much mor...   
...                                                  ...   
23476  McPain: John McCain Furious That Iran Treated ...   
23477  JUSTICE? Yahoo Settles E-mail Privacy Class-ac...   
23478  Sunnistan: US and Allied ‘Safe Zone’ Plan to T...   
23479  How to Blow $700 Million: Al Jazeera America F...   
23480  10 U.S. Navy Sailors Held by Iranian Military ...   

                                                    text       subject  \
0      WASHINGTON (Reuters) - The head of a conservat...  politicsNews   
1      WASHINGTON (Reuters) - Transgender people will...  politicsNews   
2      WASHINGTON (Reuters) - The special counsel inv...  politicsNews   
3      WASHINGTON (Reuters) - Trump campaign adviser ...  politicsNews   
4      SEATTLE/WASHINGTON (Reuters) - President Donal...  politicsNews   
...                                                  ...           ...   
23476  21st Century Wire says As 21WIRE reported earl...   Middle-east   
23477  21st Century Wire says It s a familiar theme. ...   Middle-east   
23478  Patrick Henningsen  21st Century WireRemember ...   Middle-east   
23479  21st Century Wire says Al Jazeera America will...   Middle-east   
23480  21st Century Wire says As 21WIRE predicted in ...   Middle-east   

                     date  class  
0      December 31, 2017       1  
1      December 29, 2017       1  
2      December 31, 2017       1  
3      December 30, 2017       1  
4      December 29, 2017       1  
...                   ...    ...  
23476    January 16, 2016      0  
23477    January 16, 2016      0  
23478    January 15, 2016      0  
23479    January 14, 2016      0  
23480    January 12, 2016      0  

[44898 rows x 5 columns]

### Data Assesing

In [8]:
combine.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 44898 entries, 0 to 23480
Data columns (total 5 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   title    44898 non-null  object
 1   text     44898 non-null  object
 2   subject  44898 non-null  object
 3   date     44898 non-null  object
 4   class    44898 non-null  int64 
dtypes: int64(1), object(4)
memory usage: 2.1+ MB


In [9]:
def data_assesing(data):
    print(f"Total NaN/Null Data per Column:\n{data.isna().sum().sort_values(ascending=False)}\n")
    print(f"Data Shape:\n{data.shape}")
    print(f"\nTotal Duplicated Data: {data.duplicated().sum()}")

data_assesing(combine)

Total NaN/Null Data per Column:
title      0
text       0
subject    0
date       0
class      0
dtype: int64

Data Shape:
(44898, 5)

Total Duplicated Data: 209


### Data Cleaning

In [10]:
combine = combine.drop_duplicates()
dataset = pd.DataFrame(combine.drop(columns=['title', 'subject', 'date'], axis=1))

data_assesing(dataset)

Total NaN/Null Data per Column:
text     0
class    0
dtype: int64

Data Shape:
(44689, 2)

Total Duplicated Data: 6042


### Clean Data

In [11]:
!mkdir data
dataset.to_csv("data/data.csv", index=False)

## Set Variables

In [12]:
PIPELINE_NAME = "fakenews-pipeline"
SCHEMA_PIPELINE_NAME = "fakenews-tfdv-schema"

PIPELINE_ROOT = os.path.join('pipelines', PIPELINE_NAME)

METADATA_PATH = os.path.join('metadata', PIPELINE_NAME, 'metadata.db')

SERVING_MODEL_DIR = os.path.join('serving_model', PIPELINE_NAME)

In [13]:
DATA_ROOT = "data"

In [14]:
interactive_context = InteractiveContext(pipeline_root=PIPELINE_ROOT)

## Data Ingestion

In [15]:
output = example_gen_pb2.Output(
    split_config = example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name="train", hash_buckets=8),
        example_gen_pb2.SplitConfig.Split(name="eval", hash_buckets=2)
    ])
)
example_gen = CsvExampleGen(input_base=DATA_ROOT, output_config=output)
interactive_context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}))

## Data Validation

### Create Statistics Summary

In [16]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs["examples"]
)
interactive_context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=StatisticsGen, output_key=statistics, additional_properties={}, additional_custom_properties={}))

In [17]:
interactive_context.show(statistics_gen.outputs["statistics"])

### Create Data Schema

In [18]:
schema_gen = SchemaGen(
    statistics=statistics_gen.outputs["statistics"]
)
interactive_context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 3
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}))

In [19]:
interactive_context.show(schema_gen.outputs["schema"])

Type  Presence Valency Domain
Feature name                                
'class'         INT  required              -
'text'        BYTES  required              -

### Cheking Data Anomalies

In [20]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=schema_gen.outputs['schema']
)
interactive_context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 4
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}))

In [21]:
interactive_context.show(example_validator.outputs['anomalies'])

## Data Prerprocessing

In [22]:
TRANSFORM_MODULE_FILE = "transform.py"

In [23]:
%%writefile {TRANSFORM_MODULE_FILE}

import tensorflow as tf

LABEL_KEY = "class"
FEATURE_KEY = "text"

def transformed_name(key):
     return f"{key}_xf"

def preprocessing_fn(inputs):
    outputs = {}
    outputs[transformed_name(FEATURE_KEY)] = tf.strings.lower(inputs[FEATURE_KEY])
    outputs[transformed_name(LABEL_KEY)] = tf.cast(inputs[LABEL_KEY], tf.int64)
    
    return outputs

Overwriting transform.py


In [24]:
transform = Transform(
    examples=example_gen.outputs["examples"],
    schema=schema_gen.outputs["schema"],
    module_file=os.path.abspath(TRANSFORM_MODULE_FILE)
)
interactive_context.run(transform)

Instructions for updating:
Use ref() instead.


Instructions for updating:
Use ref() instead.


INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Transform\transform_graph\5\.temp_path\tftransform_tmp\179a6cecbce8430e9a0c655efc7d8196\assets


INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Transform\transform_graph\5\.temp_path\tftransform_tmp\179a6cecbce8430e9a0c655efc7d8196\assets


INFO:tensorflow:struct2tensor is not available.


...

INFO:tensorflow:tensorflow_decision_forests is not available.


INFO:tensorflow:tensorflow_decision_forests is not available.


INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:tensorflow_text is not available.


ExecutionResult(
    component_id: Transform
    execution_id: 5
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={})
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={})
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={})
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={})
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={})
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={})
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={})
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}))

## Model Development

### Hyperparameter Tuner

In [25]:
TUNER_MODULE_FILE = "tuner.py"

In [26]:
%%writefile {TUNER_MODULE_FILE}
import keras_tuner as kt
import tensorflow as tf
import tensorflow_transform as tft
from typing import NamedTuple, Dict, Text, Any
from keras_tuner.engine import base_tuner
from tensorflow.keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs

LABEL_KEY = "class"
FEATURE_KEY = "text"
NUM_EPOCHS = 2

TunerFnResult = NamedTuple("TunerFnResult", [
    ("tuner", base_tuner.BaseTuner),
    ("fit_kwargs", Dict[Text, Any]),
])

early_stopping_callback = tf.keras.callbacks.EarlyStopping(
    monitor="val_binary_accuracy",
    mode="max",
    verbose=1,
    patience=10,
)


def transformed_name(key):
    return f"{key}_xf"


def gzip_reader_fn(filenames):
    return tf.data.TFRecordDataset(filenames, compression_type="GZIP")


def input_fn(file_pattern, tf_transform_output, num_epochs, batch_size=64):
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy()
    )
    
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY),
    )
    
    return dataset

def model_builder(hypa, vectorizer_layer):

  # Define hyperparameters (consider reducing the range if needed)
  hidden_layers = hypa.Choice("hidden_layers", values=[1, 2])
  embedding_size = hypa.Int("embedding_size", min_value=32, max_value=128, step=32)
  lstm_units = hypa.Int("lstm_units", min_value=32, max_value=128, step=32)
  dropout_rate = hypa.Float("dropout_rate", min_value=0.2, max_value=0.5, step=0.1)
  dense_units = hypa.Int("dense_units", min_value=32, max_value=128, step=32)  # New hyperparameter

  # Model construction
  inputs = tf.keras.Input(shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string)

  x = vectorizer_layer(inputs)
  x = layers.Embedding(5000, embedding_size)(x)
  x = layers.Bidirectional(layers.LSTM(lstm_units))(x)

  # Add dense layers based on hyperparameter
  for _ in range(hidden_layers):
    x = layers.Dense(dense_units, activation="relu")(x)  # Use dense_units hyperparameter
    x = layers.Dropout(dropout_rate)(x)

  outputs = layers.Dense(1, activation="sigmoid")(x)

  model = tf.keras.Model(inputs=inputs, outputs=outputs)

  # Compile for binary classification (consider learning rate tuning)
  model.compile(
      optimizer=tf.keras.optimizers.Adam(learning_rate=1e-4),  # Consider hyperparameter tuning
      loss="binary_crossentropy",
      metrics=["accuracy"],
  )

  return model


def tuner_fn(fn_args):
  # Load the transform graph
  tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

  # Create training and evaluation datasets with transformed features
  train_set = input_fn(fn_args.train_files[0], tf_transform_output, NUM_EPOCHS)
  eval_set = input_fn(fn_args.eval_files[0], tf_transform_output, NUM_EPOCHS)

  # Extract text features for vectorization
  vectorizer_dataset = train_set.map(lambda f, l: f[transformed_name(FEATURE_KEY)])

  # Define and adapt the text vectorization layer
  vectorizer_layer = layers.TextVectorization(
      max_tokens=1000, output_mode="int", output_sequence_length=100
  )
  vectorizer_layer.adapt(vectorizer_dataset)

  # Create a Hyperband tuner with the vectorization layer
  tuner = kt.Hyperband(
      hypermodel=lambda hypa: model_builder(hypa, vectorizer_layer),
      objective=kt.Objective("accuracy", direction="max"),
      max_epochs=NUM_EPOCHS,
      factor=3,
      directory=fn_args.working_dir,
      project_name="kt_hyperband",
  )

  # Define fit arguments with early stopping callback
  fit_kwargs = {
      "callbacks": [early_stopping_callback],
      "x": train_set,
      "validation_data": eval_set,
      "steps_per_epoch": fn_args.train_steps,
      "validation_steps": fn_args.eval_steps,
  }

  return TunerFnResult(tuner=tuner, fit_kwargs=fit_kwargs)

Overwriting tuner.py


In [27]:
tuner = Tuner(
    module_file=os.path.abspath(TUNER_MODULE_FILE),
    examples=transform.outputs["transformed_examples"],
    transform_graph=transform.outputs["transform_graph"],
    schema=schema_gen.outputs["schema"],
    train_args=trainer_pb2.TrainArgs(splits=["train"], num_steps=500),
    eval_args=trainer_pb2.EvalArgs(splits=["eval"], num_steps=200),
)
interactive_context.run(tuner)

Trial 2 Complete [00h 06m 57s]
accuracy: 0.9897500276565552

Best accuracy So Far: 0.9897812604904175
Total elapsed time: 00h 22m 47s
INFO:tensorflow:Oracle triggered exit


INFO:tensorflow:Oracle triggered exit


Results summary
Results in pipelines\fakenews-pipeline\.temp\6\kt_hyperband
Showing 10 best trials
Trial summary
Hyperparameters:
hidden_layers: 1
embedding_size: 128
lstm_units: 96
dropout_rate: 0.4000000000000001
dense_units: 32
tuner/epochs: 2
tuner/initial_epoch: 0
tuner/bracket: 0
tuner/round: 0
Score: 0.9897812604904175
Trial summary
Hyperparameters:
hidden_layers: 2
embedding_size: 96
lstm_units: 96
dropout_rate: 0.30000000000000004
dense_units: 64
tuner/epochs: 2
tuner/initial_epoch: 0
tuner/bracket: 0
tuner/round: 0
Score: 0.9897500276565552


ExecutionResult(
    component_id: Tuner
    execution_id: 6
    outputs:
        best_hyperparameters: OutputChannel(artifact_type=HyperParameters, producer_component_id=Tuner, output_key=best_hyperparameters, additional_properties={}, additional_custom_properties={})
        tuner_results: OutputChannel(artifact_type=TunerResults, producer_component_id=Tuner, output_key=tuner_results, additional_properties={}, additional_custom_properties={}))

### Training Model

In [28]:
TRAINER_MODULE_FILE = "trainer.py"

In [29]:
%%writefile {TRAINER_MODULE_FILE}
import os
import tensorflow as tf
import tensorflow_transform as tft
import tensorflow_hub as hub
from tensorflow.keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs


LABEL_KEY = "class"
FEATURE_KEY = "text"


def transformed_name(key): 
    return f"{key}_xf"


def gzip_reader_fn(filenames):
    return tf.data.TFRecordDataset(filenames, compression_type="GZIP")


def input_fn(file_pattern, tf_transform_output, num_epochs, batch_size=64):
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy()
    )
    
    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY),
    )
    
    return dataset

def model_builder(vectorizer_layer, hp):
    inputs = tf.keras.Input(
        shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string
    )

    x = vectorizer_layer(inputs)
    x = layers.Embedding(input_dim=5000, output_dim=hp["embedding_size"])(x)
    x = layers.Bidirectional(layers.LSTM(hp["lstm_units"]))(x)

    for _ in range(hp["hidden_layers"]):
        x = layers.Dense(hp["dense_units"], activation=tf.nn.relu)(x)
        x = layers.Dropout(hp["dropout_rate"])(x)

    outputs = layers.Dense(1, activation=tf.nn.sigmoid)(x)
    
    model = tf.keras.Model(inputs=inputs, outputs = outputs)

    model.compile(
        optimizer=tf.keras.optimizers.Adam(learning_rate=1e-4),
        loss=tf.keras.losses.BinaryCrossentropy(),
        metrics=[tf.keras.metrics.BinaryAccuracy()],
    )
    
    model.summary()
    
    return model

def _get_serve_tf_example_fn(model, tf_transform_output):
    model.tft_layer = tf_transform_output.transform_features_layer()
    
    @tf.function
    def serve_tf_examples_fn(serialized_tf_examples):
        feature_spec = tf_transform_output.raw_feature_spec()
        feature_spec.pop(LABEL_KEY)
        
        parsed_features = tf.io.parse_example(
            serialized_tf_examples, feature_spec
        )
        transformed_features = model.tft_layer(parsed_features)
        
        # get predictions using transformed features
        return model(transformed_features)
    
    return serve_tf_examples_fn


def run_fn(fn_args: FnArgs):
  # Extract hyperparameters
  hyperparameters = fn_args.hyperparameters["values"]

  # Define log directory and callbacks
  log_dir = os.path.join(os.path.dirname(fn_args.serving_model_dir), "logs")
  callbacks = [
      tf.keras.callbacks.TensorBoard(log_dir=log_dir, update_freq="batch"),
      tf.keras.callbacks.EarlyStopping(
          monitor="val_binary_accuracy", mode="max", verbose=1, patience=10
      ),
      tf.keras.callbacks.ModelCheckpoint(
          fn_args.serving_model_dir,
          monitor="val_binary_accuracy",
          mode="max",
          verbose=1,
          save_best_only=True,
      ),
  ]

  # Load transform graph and create datasets
  tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)
  train_set = input_fn(fn_args.train_files, tf_transform_output, hyperparameters["tuner/epochs"])
  eval_set = input_fn(fn_args.eval_files, tf_transform_output, hyperparameters["tuner/epochs"])
  vectorizer_dataset = train_set.map(lambda f, l: f[transformed_name(FEATURE_KEY)])

  # Define and adapt vectorization layer
  vectorizer_layer = layers.TextVectorization(
      max_tokens=5000, output_mode="int", output_sequence_length=500
  )
  vectorizer_layer.adapt(vectorizer_dataset)

  # Build model using hyperparameters
  model = model_builder(vectorizer_layer, hyperparameters)

  # Train the model with callbacks
  model.fit(
      x=train_set,
      steps_per_epoch=fn_args.train_steps,
      validation_data=eval_set,
      validation_steps=fn_args.eval_steps,
      callbacks=callbacks,
      epochs=hyperparameters["tuner/epochs"],
      verbose=1,
  )

  # Define serving signature and save the model
  signatures = {
      "serving_default": _get_serve_tf_example_fn(model, tf_transform_output).get_concrete_function(
          tf.TensorSpec(shape=[None], dtype=tf.string, name="examples")
      )
  }
  model.save(fn_args.serving_model_dir, save_format="tf", signatures=signatures)


Overwriting trainer.py


In [30]:
trainer = Trainer(
    module_file=os.path.abspath(TRAINER_MODULE_FILE),
    examples=transform.outputs["transformed_examples"],
    transform_graph=transform.outputs["transform_graph"],
    schema=schema_gen.outputs["schema"],
    hyperparameters=tuner.outputs['best_hyperparameters'],
    train_args=trainer_pb2.TrainArgs(splits=["train"], num_steps=500),
    eval_args=trainer_pb2.EvalArgs(splits=["eval"], num_steps=200),
)
interactive_context.run(trainer)

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 text_xf (InputLayer)        [(None, 1)]               0         
                                                                 
 text_vectorization (TextVec  (None, 500)              0         
 torization)                                                     
                                                                 
 embedding_1 (Embedding)     (None, 500, 128)          640000    
                                                                 
 bidirectional_1 (Bidirectio  (None, 192)              172800    
 nal)                                                            
                                                                 
 dense_3 (Dense)             (None, 32)                6176      
                                                                 
 dropout_2 (Dropout)         (None, 32)                0   

INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Trainer\model\7\Format-Serving\assets


INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Trainer\model\7\Format-Serving\assets


500/500 [==============================] - 2415s 5s/step - loss: 0.3387 - binary_accuracy: 0.8808 - val_loss: 0.0850 - val_binary_accuracy: 0.9765
Epoch 2/2
500/500 [==============================] - ETA: 0s - loss: 0.0408 - binary_accuracy: 0.9912
Epoch 2: val_binary_accuracy improved from 0.97648 to 0.98687, saving model to pipelines\fakenews-pipeline\Trainer\model\7\Format-Serving


INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Trainer\model\7\Format-Serving\assets


...

INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:tensorflow_text is not available.


INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Trainer\model\7\Format-Serving\assets


INFO:tensorflow:Assets written to: pipelines\fakenews-pipeline\Trainer\model\7\Format-Serving\assets


ExecutionResult(
    component_id: Trainer
    execution_id: 7
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={})
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}))

## Analysis and Validation Model

In [31]:
model_resolver = Resolver(
    strategy_class=LatestBlessedModelStrategy,
    model=Channel(type=Model),
    model_blessing=Channel(type=ModelBlessing),
).with_id("Latest_blessed_model_resolver")

interactive_context.run(model_resolver)

ExecutionResult(
    component_id: Latest_blessed_model_resolver
    execution_id: 8
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Latest_blessed_model_resolver, output_key=model, additional_properties={}, additional_custom_properties={})
        model_blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Latest_blessed_model_resolver, output_key=model_blessing, additional_properties={}, additional_custom_properties={}))

In [32]:
import tensorflow_model_analysis as tfma 
 
eval_config = tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='class')],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            
            tfma.MetricConfig(class_name='ExampleCount'),
            tfma.MetricConfig(class_name='AUC'),
            tfma.MetricConfig(class_name='FalsePositives'),
            tfma.MetricConfig(class_name='TruePositives'),
            tfma.MetricConfig(class_name='FalseNegatives'),
            tfma.MetricConfig(class_name='TrueNegatives'),
            tfma.MetricConfig(class_name='BinaryAccuracy',
                threshold=tfma.MetricThreshold(
                    value_threshold=tfma.GenericValueThreshold(
                        lower_bound={'value':0.5}),
                    change_threshold=tfma.GenericChangeThreshold(
                        direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                        absolute={'value':0.0001})
                    )
            )
        ])
    ]
 
)

## Evaluation Model

In [33]:
evaluator = Evaluator(
    examples=example_gen.outputs["examples"],
    model=trainer.outputs["model"],
    baseline_model=model_resolver.outputs["model"],
    eval_config=eval_config,
)
interactive_context.run(evaluator)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Evaluator
    execution_id: 9
    outputs:
        evaluation: OutputChannel(artifact_type=ModelEvaluation, producer_component_id=Evaluator, output_key=evaluation, additional_properties={}, additional_custom_properties={})
        blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Evaluator, output_key=blessing, additional_properties={}, additional_custom_properties={}))

In [34]:
eval_result = evaluator.outputs['evaluation'].get()[0].uri
tfma_result = tfma.load_eval_result(eval_result)
tfma.view.render_slicing_metrics(tfma_result)
tfma.addons.fairness.view.widget_view.render_fairness_indicator(
    tfma_result
)

FairnessIndicatorViewer(slicingMetrics=[{'sliceValue': 'Overall', 'slice': 'Overall', 'metrics': {'binary_accu…

## Export Model

In [35]:
from tfx.components import Pusher 
from tfx.proto import pusher_pb2 
 
pusher = Pusher(
model=trainer.outputs['model'],
model_blessing=evaluator.outputs['blessing'],
push_destination=pusher_pb2.PushDestination(
    filesystem=pusher_pb2.PushDestination.Filesystem(
        base_directory='serving_model_dir/fakenews-detection-model'))
 
)
 
interactive_context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 10
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}))